In [1]:
import pandas as pd
from chart_studio.plotly import iplot
import cufflinks
from IPython.core.interactiveshell import InteractiveShell
import plotly.figure_factory as ff
InteractiveShell.ast_node_interactivity = 'all'
cufflinks.go_offline()
cufflinks.set_config_file(world_readable=True, theme='pearl')

In [2]:
from chart_studio.plotly import plot_mpl
from statsmodels.tsa.seasonal import seasonal_decompose

In [3]:
import quandl

In [19]:
quandlsent = quandl.get('AAII/AAII_SENTIMENT', start_date='2005-01-05', end_date='2020-01-06')

In [21]:
quandlsent = quandlsent[['Bullish','Neutral','Bearish','Bullish Average']]

In [14]:
quandlsent.reset_index(inplace=True)

In [22]:
quandlsent

Bullish   Neutral   Bearish  Bullish Average
Date                                                     
2005-01-06  0.381000  0.273800  0.345200         0.384907
2005-01-13  0.339900  0.261400  0.398700         0.384907
2005-01-20  0.336600  0.326700  0.336600         0.384907
2005-01-27  0.264300  0.371400  0.364300         0.384907
2005-02-03  0.416700  0.333300  0.250000         0.384907
...              ...       ...       ...              ...
2019-12-05  0.317152  0.391586  0.291262         0.380745
2019-12-12  0.376316  0.363158  0.260526         0.380745
2019-12-19  0.440945  0.354331  0.204724         0.380745
2019-12-26  0.418879  0.365782  0.215339         0.380745
2020-01-02  0.372159  0.409091  0.218750         0.380745

[783 rows x 4 columns]

In [75]:
quandlsent.iplot(title='AAII Investor Sentiment Survey: %of people who believe the market will... in the next six months')

# Some extra external variables such as P/E ratio, Dividend Yield and Earning Per Share

In [27]:
divyield = quandl.get('MULTPL/SP500_DIV_YIELD_MONTH')

In [28]:
divyield =  divyield.tail(121)

In [29]:
divyield.rename(columns={'Value': 'Dividendyield'}, inplace= True)

In [59]:
sp500bymonth = quandl.get('MULTPL/SP500_REAL_PRICE_MONTH')

In [60]:
sp500bymonth = sp500bymonth.tail(122)

In [61]:
sp500bymonth.rename(columns={'Value': 'SP500price'}, inplace= True)

In [33]:
peratiomonth = quandl.get('MULTPL/SP500_PE_RATIO_MONTH')

In [38]:
peratiomonth = peratiomonth.tail(122)

In [57]:
earningmonth = quandl.get('MULTPL/SP500_EARNINGS_YIELD_MONTH')


In [56]:
eps = earningmonth.tail(122)

NameError: name 'earningmonth' is not defined

In [35]:
adj_sp500 = quandl.get('MULTPL/SP500_INFLADJ_MONTH')

In [36]:
adj_sp500 = adj_sp500.tail(122)

In [37]:
adj_sp500.rename(columns={'Value': 'Adj_Price'}, inplace= True)

In [39]:
peratiomonth.rename(columns={'Value': 'P/E'}, inplace= True)

In [44]:
eps.rename(columns = { 'Value': 'EPS'},inplace =True) 

In [45]:
extra = pd.concat([eps,peratiomonth,divyield],axis=1)

In [79]:
extra = pd.concat([extra,sp500bymonth],axis=1)

In [81]:
extra = extra.fillna(method='ffill')

In [85]:
extra

EPS    P/E  Dividendyield  SP500price
Date                                              
2010-01-01  4.83  20.70            NaN     1123.58
2010-01-31  4.83  20.70           1.98     1123.58
2010-02-01  5.29  18.91           1.98     1089.16
2010-02-28  5.29  18.91           2.03     1089.16
2010-03-01  5.29  18.91           2.03     1152.05
...          ...    ...            ...         ...
2019-10-31  4.48  22.31           1.92     2977.68
2019-11-01  4.30  23.26           1.87     3104.90
2019-11-30  4.30  23.26           1.84     3104.90
2019-12-01  4.22  23.68           1.84     3159.85
2019-12-31  4.13  24.21           1.81     3230.58

[240 rows x 4 columns]

In [172]:
extra.iloc[210,]

EPS                 4.71
P/E                21.25
Dividendyield       1.80
SP500price       2785.46
Name: 2018-10-01 00:00:00, dtype: float64

In [212]:
extra[['P/E','EPS']].iplot(y='P/E', secondary_y='EPS',
                                                 yTitle='P/E', secondary_y_title='EPS',
                                                 title='P/E versus Earnings')

In [156]:
extra.iplot(
    xTitle='Date',
    title='Total EPS, P/E, DividendYield')

In [4]:
df = pd.read_csv('totaldf.csv')

## Add year and month column

In [4]:
import yfinance as yf
data = yf.download("^GSPC", start="2010-01-06", end="2020-01-06",
                   group_by="ticker")
data= data.reset_index()

[*********************100%***********************]  1 of 1 completed


In [5]:
data['year-month'] = [pd.datetime(year, month, 1) for year, month in zip(
    data['Date'].dt.year, data['Date'].dt.month)]

In [6]:
data['year'] = pd.DatetimeIndex(data['Date']).year
data['month'] = pd.DatetimeIndex(data['Date']).month

In [7]:
monthly = data.groupby('year-month')['Close'].count().reset_index()

# Bargraph displaying trading volume by year and by month

In [34]:
data.groupby(data['year'])['Volume'].sum().iplot(kind='bar', colorscale='set2',
                                                 xTitle='Year',
                                                 yTitle='Number of Volume Traded total by Year',
                                                 title='Bar plot of total trading volume by Year')


In [35]:
data.groupby(data['month'])['Volume'].sum().iplot(kind='bar', colorscale='set2',
                                                 xTitle='Month',
                                                 yTitle='Number of Volume Traded total by Month',
                                                 title='Bar plot of total trading volume by Month')


# Histogram Distribution of S&P 500 prices

In [57]:
df[['Open','High','Close']].iplot(
    kind='hist',
    bins=30,
    xTitle='sp500 index',
    linecolor='black',
    yTitle='count',
    title='SP500 Distribution')

In [12]:
df.Date = pd.to_datetime(df.Date)

In [13]:
df['year-month'] = [
    pd.datetime(year, month, 1) for year, month in zip(
        df['Date'].dt.year, df['Date'].dt.month)]

In [22]:
monthly = df.groupby('year-month')['Close'].mean().reset_index()

In [71]:
from chart_studio.plotly import iplot
import chart_studio


In [72]:
chart_studio.tools.set_credentials_file(username='rockinghummingbird', api_key='n5q3IhAz1iKjZzgVWXI8')


In [97]:
totaldf = pd.read_csv('totaldf.csv')

In [103]:
totaldf.index = totaldf.Date

# S&P prices trend with range slide

In [221]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=df.Date, y=df['High'], name="High",
                         line_color='deepskyblue'))

fig.add_trace(go.Scatter(x=df.Date, y=df['Low'], name="Low",
                         line_color='dimgray'))

fig.update_layout(title_text='SP 500 Time Series with Rangeslider',
                  xaxis_rangeslider_visible=True)
fig.show()

# Seasonality in Trends

In [157]:
spivot

year          2009         2010         2011         2012         2013  \
month                                                                    
1       858.458889  1123.581582  1282.618500  1300.578015  1480.395240   
2       805.227369  1089.159989  1321.117888  1352.487500  1512.311581   
3       757.126814  1152.048690  1304.486514  1389.240001  1550.828986   
4       848.151899  1197.316185  1331.505011  1386.428986  1570.702265   
5       902.408502  1125.062006  1338.310465  1341.272716  1639.842723   
6       926.115001  1083.360895  1287.288641  1323.484294  1618.772516   
7       935.821364  1079.803336  1325.184503  1359.776199  1668.675443   
8      1009.724758  1087.282271  1185.305653  1403.448258  1670.093639   
9      1044.552383  1122.081903  1173.879057  1443.419472  1687.173505   
10     1067.663630  1171.583810  1207.216187  1437.816662  1720.026532   
11     1088.069006  1198.888561  1226.414772  1394.512387  1783.541003   
12     1110.377724  1241.525452  1243.322847  1422.285492  1807.775234   

year          2014         2015         2016         2017         2018  \
month                                                                    
1      1822.356660  2028.178510  1918.597888  2275.115979  2789.803816   
2      1817.034739  2082.195794  1904.418494  2329.910542  2705.155248   
3      1863.523339  2079.990440  2021.954090  2366.822170  2702.773821   
4      1864.263335  2094.862839  2075.535232  2359.309455  2653.625209   
5      1889.767142  2111.943518  2065.550479  2395.345881  2701.493619   
6      1947.087612  2099.283658  2083.891369  2433.985451  2754.352888   
7      1973.099987  2094.143627  2148.901978  2454.102502  2793.643357   
8      1961.531907  2039.866205  2177.482167  2456.223070  2857.820429   
9      1993.226190  1944.402384  2157.690964  2492.841040  2901.500514   
10     1937.274350  2024.812716  2143.020938  2556.997270  2785.464780   
11     2044.572105  2080.616504  2164.985689  2593.605736  2723.231422   
12     2054.266363  2054.079562  2246.629046  2664.340527  2567.307386   

year          2019         2020  
month                            
1      2607.389997  3246.326742  
2      2754.864206          NaN  
3      2803.983794          NaN  
4      2903.799979          NaN  
5      2854.705910          NaN  
6      2890.165979          NaN  
7      2996.113636          NaN  
8      2897.450451          NaN  
9      2982.156006          NaN  
10     2977.675197          NaN  
11     3104.904492          NaN  
12     3176.749512          NaN

In [161]:
SP500

Open         High          Low        Close    Adj Close  \
Date                                                                          
2009-01-06   931.169983   943.849976   927.280029   934.700012   934.700012   
2009-01-07   927.450012   927.450012   902.369995   906.650024   906.650024   
2009-01-08   905.729980   910.000000   896.809998   909.729980   909.729980   
2009-01-09   909.909973   911.929993   888.309998   890.349976   890.349976   
2009-01-12   890.400024   890.400024   864.320007   870.260010   870.260010   
...                 ...          ...          ...          ...          ...   
2019-12-30  3240.090088  3240.919922  3216.570068  3221.290039  3221.290039   
2019-12-31  3215.179932  3231.719971  3212.030029  3230.780029  3230.780029   
2020-01-02  3244.669922  3258.139893  3235.530029  3257.850098  3257.850098   
2020-01-03  3226.360107  3246.149902  3222.340088  3234.850098  3234.850098   
2020-01-06  3217.550049  3246.840088  3214.639893  3246.280029  3246.280029   

                Volume  
Date                    
2009-01-06  5392620000  
2009-01-07  4704940000  
2009-01-08  4991550000  
2009-01-09  4716500000  
2009-01-12  4725050000  
...                ...  
2019-12-30  3013290000  
2019-12-31  2893810000  
2020-01-02  3458250000  
2020-01-03  3461290000  
2020-01-06  3674070000  

[2769 rows x 6 columns]

In [12]:
import numpy as np

In [29]:
spivot = pd.pivot_table(data, index='month', columns = 'year', 
                        values = 'Adj Close', aggfunc=np.mean)
spivot.iplot(title = 'Yearly Trends', mode='lines+markers',
    opacity=10,
    size=10,
    symbol=2)


In [21]:
import seaborn as sns
import matplotlib.pyplot as plt

In [173]:
diff = sp500.diff(periods=1)

In [178]:
diff.corr()

Open      High       Low     Close  Adj Close    Volume  \
Open       1.000000  0.656712  0.603963  0.125137   0.125137 -0.010758   
High       0.656712  1.000000  0.715676  0.638409   0.638409  0.070234   
Low        0.603963  0.715676  1.000000  0.697548   0.697548 -0.185080   
Close      0.125137  0.638409  0.697548  1.000000   1.000000 -0.077361   
Adj Close  0.125137  0.638409  0.697548  1.000000   1.000000 -0.077361   
Volume    -0.010758  0.070234 -0.185080 -0.077361  -0.077361  1.000000   
year      -0.013809  0.033946 -0.009390  0.034072   0.034072  0.100943   
month      0.009423 -0.027094 -0.001874 -0.030441  -0.030441 -0.109876   

               year     month  
Open      -0.013809  0.009423  
High       0.033946 -0.027094  
Low       -0.009390 -0.001874  
Close      0.034072 -0.030441  
Adj Close  0.034072 -0.030441  
Volume     0.100943 -0.109876  
year       1.000000 -0.959335  
month     -0.959335  1.000000

In [6]:
sp500 = data.copy()

In [14]:
sp500['Daily Lag'] = sp500['Close'].shift(1)


Date         Open         High          Low        Close  \
0    2010-01-06  1135.709961  1139.189941  1133.949951  1137.140015   
1    2010-01-07  1136.270020  1142.459961  1131.319946  1141.689941   
2    2010-01-08  1140.520020  1145.390015  1136.219971  1144.979980   
3    2010-01-11  1145.959961  1149.739990  1142.020020  1146.979980   
4    2010-01-12  1143.810059  1143.810059  1131.770020  1136.219971   
...         ...          ...          ...          ...          ...   
2512 2019-12-30  3240.090088  3240.919922  3216.570068  3221.290039   
2513 2019-12-31  3215.179932  3231.719971  3212.030029  3230.780029   
2514 2020-01-02  3244.669922  3258.139893  3235.530029  3257.850098   
2515 2020-01-03  3226.360107  3246.149902  3222.340088  3234.850098   
2516 2020-01-06  3217.550049  3246.840088  3214.639893  3246.280029   

        Adj Close      Volume    Daily Lag  
0     1137.140015  4972660000          NaN  
1     1141.689941  5270680000  1137.140015  
2     1144.979980  4389590000  1141.689941  
3     1146.979980  4255780000  1144.979980  
4     1136.219971  4716160000  1146.979980  
...           ...         ...          ...  
2512  3221.290039  3013290000  3240.020020  
2513  3230.780029  2893810000  3221.290039  
2514  3257.850098  3458250000  3230.780029  
2515  3234.850098  3461290000  3257.850098  
2516  3246.280029  3674070000  3234.850098  

[2517 rows x 8 columns]

In [12]:
(1 + dr).cumprod()

0            NaN
1       1.004001
2       1.006894
3       1.008653
4       0.999191
          ...   
2512    2.832800
2513    2.841145
2514    2.864951
2515    2.844725
2516    2.854776
Name: Close, Length: 2517, dtype: float64

In [9]:
dr = sp500.Close.pct_change()

0                NaN
1       3.504631e-06
2       2.516836e-06
3       1.522917e-06
4      -8.256470e-06
            ...     
2512   -1.794568e-06
2513    9.118608e-07
2514    2.571881e-06
2515   -2.182441e-06
2516    1.088437e-06
Name: Close, Length: 2517, dtype: float64

In [8]:
sp500.Close.pct_change().iplot()

In [186]:
sp500['DailyReturns'] = (sp500['Daily Lag']/sp500['Close']) -1


In [187]:
sp500.DailyReturns.iplot()

In [24]:
mov = data['Close'].rolling(window=30).mean()

In [25]:
mov

0               NaN
1               NaN
2               NaN
3               NaN
4               NaN
           ...     
2512    3157.822982
2513    3161.500317
2514    3166.027653
2515    3169.849992
2516    3174.443994
Name: Close, Length: 2517, dtype: float64

In [26]:
data['Close'].rolling(window=30).mean().iplot(title='30 Day Avg')
data['Close'].iplot()

# SIMPLE MOVING AVERAGE for different time periods

In [33]:
data['Close'].ta_plot(study='sma',periods=[12,24,55,100,200], title='Simple Moving Averages')


# Exponential Moving Average for different time periods

In [32]:
data['Close'].ta_plot(study='ema',periods=[12,100,200], name='Exponential Moving Averages')


In [24]:
data['changepercentage'] =  (data['Adj Close'] - data['Open']) / data['Adj Close'] * 100

In [94]:
buy = pd.read_csv('buy.csv',index_col= 0)

In [95]:
sell = pd.read_csv('sell.csv', index_col = 0)

In [96]:
buy = buy[1:].reset_index()

In [97]:
buy.rename(columns={'index': 'Date'}, inplace= True)

In [98]:
sell = sell[1:].reset_index()

In [99]:
sell.rename(columns={'index': 'Date'}, inplace= True)

In [101]:
sell.rename(columns={'Category: All categories': 'sell'}, inplace= True)

In [100]:
buy.rename(columns={'Category: All categories': 'buy'}, inplace= True)

In [102]:
buy

Date buy
0    2010-01  43
1    2010-02  44
2    2010-03  46
3    2010-04  47
4    2010-05  38
..       ...  ..
116  2019-09  49
117  2019-10  49
118  2019-11  54
119  2019-12  56
120  2020-01  82

[121 rows x 2 columns]

In [103]:
sell

Date sell
0    2010-01   38
1    2010-02   39
2    2010-03   41
3    2010-04   47
4    2010-05   43
..       ...  ...
116  2019-09   61
117  2019-10   64
118  2019-11   71
119  2019-12   80
120  2020-01   88

[121 rows x 2 columns]

In [105]:
buyselldf = pd.merge(buy, sell, on= 'Date')

In [116]:
buyselldf.Date = pd.to_datetime(buyselldf.Date)

In [113]:
sp500bymonth = sp500bymonth.reset_index()

In [115]:
sp500bymonth.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 122 entries, 0 to 121
Data columns (total 2 columns):
Date          122 non-null datetime64[ns]
SP500price    122 non-null float64
dtypes: datetime64[ns](1), float64(1)
memory usage: 2.0 KB


In [118]:
pricebymonth = pd.merge(sp500bymonth, buyselldf)

In [126]:
pricebymonth.index = pricebymonth.Date

In [130]:
pricebymonth.drop('Date',axis = 1, inplace = True)


In [143]:
pricebymonth

SP500price   buy  sell
Date                              
2010-01-01     1123.58  43.0  38.0
2010-02-01     1089.16  44.0  39.0
2010-03-01     1152.05  46.0  41.0
2010-04-01     1197.32  47.0  47.0
2010-05-01     1125.06  38.0  43.0
...                ...   ...   ...
2019-08-01     2897.50  51.0  70.0
2019-09-01     2982.16  49.0  61.0
2019-10-01     2977.68  49.0  64.0
2019-11-01     3104.90  54.0  71.0
2019-12-01     3159.85  56.0  80.0

[120 rows x 3 columns]

In [142]:
pricebymonth.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 120 entries, 2010-01-01 to 2019-12-01
Data columns (total 3 columns):
SP500price    120 non-null float64
buy           120 non-null float64
sell          120 non-null float64
dtypes: float64(3)
memory usage: 8.8 KB


In [141]:
pricebymonth['buy'] = pricebymonth['buy'].astype(float)
pricebymonth['sell'] = pricebymonth['sell'].astype(float)


In [161]:
pricebymonth[['buy', 'sell']].iplot( title = 'Buy Stock vs Sell Stocks Google trends')
 

In [190]:
import yfinance as yf
sp500 = yf.download("^GSPC", start="2010-01-06", end="2020-01-31",
                   group_by="ticker")

[*********************100%***********************]  1 of 1 completed


In [191]:
sp500

Open         High          Low        Close    Adj Close  \
Date                                                                          
2010-01-06  1135.709961  1139.189941  1133.949951  1137.140015  1137.140015   
2010-01-07  1136.270020  1142.459961  1131.319946  1141.689941  1141.689941   
2010-01-08  1140.520020  1145.390015  1136.219971  1144.979980  1144.979980   
2010-01-11  1145.959961  1149.739990  1142.020020  1146.979980  1146.979980   
2010-01-12  1143.810059  1143.810059  1131.770020  1136.219971  1136.219971   
...                 ...          ...          ...          ...          ...   
2020-01-13  3271.129883  3288.129883  3268.429932  3288.129883  3288.129883   
2020-01-14  3285.350098  3294.250000  3277.189941  3283.149902  3283.149902   
2020-01-15  3282.270020  3298.659912  3280.689941  3289.290039  3289.290039   
2020-01-16  3302.969971  3317.110107  3302.820068  3316.810059  3316.810059   
2020-01-17  3323.659912  3329.879883  3318.860107  3329.620117  3329.620117   

                Volume  
Date                    
2010-01-06  4972660000  
2010-01-07  5270680000  
2010-01-08  4389590000  
2010-01-11  4255780000  
2010-01-12  4716160000  
...                ...  
2020-01-13  3456380000  
2020-01-14  3665130000  
2020-01-15  3716840000  
2020-01-16  3535080000  
2020-01-17  3698170000  

[2526 rows x 6 columns]

In [225]:
volumemonthlychange = sp500.Volume.resample('M').mean()


In [226]:
volumemonthlychange = volumemonthlychange[:-1]

In [229]:
volumemonthlychange = volumemonthlychange.reset_index()

In [230]:
volumemonthlychange

Date        Volume
0   2010-01-31  4.968539e+09
1   2010-02-28  4.450597e+09
2   2010-03-31  4.507980e+09
3   2010-04-30  5.559139e+09
4   2010-05-31  6.383139e+09
..         ...           ...
115 2019-08-31  3.618156e+09
116 2019-09-30  3.699616e+09
117 2019-10-31  3.372372e+09
118 2019-11-30  3.608996e+09
119 2019-12-31  3.431143e+09

[120 rows x 2 columns]

In [218]:
volseries

0      4.968539e+09
1      4.450597e+09
2      4.507980e+09
3      5.559139e+09
4      6.383139e+09
           ...     
115    3.618156e+09
116    3.699616e+09
117    3.372372e+09
118    3.608996e+09
119    3.431143e+09
Name: Volume, Length: 120, dtype: float64

In [236]:
  
# Using 'Address' as the column name 
# and equating it to the list 
pricebymonth['volchange'] = vol
  

In [235]:
vol = volumemonthlychange.Volume.to_list()

In [ ]:
pricebymonth.volchange.as

In [246]:
sp500

Open         High          Low        Close    Adj Close  \
Date                                                                          
2010-01-06  1135.709961  1139.189941  1133.949951  1137.140015  1137.140015   
2010-01-07  1136.270020  1142.459961  1131.319946  1141.689941  1141.689941   
2010-01-08  1140.520020  1145.390015  1136.219971  1144.979980  1144.979980   
2010-01-11  1145.959961  1149.739990  1142.020020  1146.979980  1146.979980   
2010-01-12  1143.810059  1143.810059  1131.770020  1136.219971  1136.219971   
...                 ...          ...          ...          ...          ...   
2020-01-13  3271.129883  3288.129883  3268.429932  3288.129883  3288.129883   
2020-01-14  3285.350098  3294.250000  3277.189941  3283.149902  3283.149902   
2020-01-15  3282.270020  3298.659912  3280.689941  3289.290039  3289.290039   
2020-01-16  3302.969971  3317.110107  3302.820068  3316.810059  3316.810059   
2020-01-17  3323.659912  3329.879883  3318.860107  3329.620117  3329.620117   

                Volume  
Date                    
2010-01-06  4972660000  
2010-01-07  5270680000  
2010-01-08  4389590000  
2010-01-11  4255780000  
2010-01-12  4716160000  
...                ...  
2020-01-13  3456380000  
2020-01-14  3665130000  
2020-01-15  3716840000  
2020-01-16  3535080000  
2020-01-17  3698170000  

[2526 rows x 6 columns]

In [237]:
pricebymonth

SP500price   buy  sell     volchange
Date                                            
2010-01-01     1123.58  43.0  38.0  4.968539e+09
2010-02-01     1089.16  44.0  39.0  4.450597e+09
2010-03-01     1152.05  46.0  41.0  4.507980e+09
2010-04-01     1197.32  47.0  47.0  5.559139e+09
2010-05-01     1125.06  38.0  43.0  6.383139e+09
...                ...   ...   ...           ...
2019-08-01     2897.50  51.0  70.0  3.618156e+09
2019-09-01     2982.16  49.0  61.0  3.699616e+09
2019-10-01     2977.68  49.0  64.0  3.372372e+09
2019-11-01     3104.90  54.0  71.0  3.608996e+09
2019-12-01     3159.85  56.0  80.0  3.431143e+09

[120 rows x 4 columns]

In [194]:
volumenchange = pd.DataFrame(volumemonthlychange)

In [198]:
volumenchange['volchange'] = volumenchange['volchange'].astype(float)


In [247]:
volumenchange.iplot()

In [241]:
pricebymonth[['buy','sell','volchange']].iplot(
    xTitle='Date',
    secondary_y='volchange',
    secondary_y_title='Average Monthly Traded Volume',
    yTitle='Google search on buy and sell',
    title='Monthly Averages')

In [243]:
pricebymonth['dev'] = pricebymonth['buy'] - pricebymonth['sell']

In [245]:
pricebymonth.corr()

SP500price       buy      sell  volchange       dev
SP500price    1.000000  0.671467  0.763973  -0.416892 -0.300415
buy           0.671467  1.000000  0.882861  -0.105166  0.093021
sell          0.763973  0.882861  1.000000  -0.117389 -0.385473
volchange    -0.416892 -0.105166 -0.117389   1.000000  0.042250
dev          -0.300415  0.093021 -0.385473   0.042250  1.000000

In [175]:
volumemonthlychange.iplot()